In [1]:
from urllib import request
from bs4 import BeautifulSoup
import nltk, re, pprint
from nltk import word_tokenize, sent_tokenize
import pandas as pd
import numpy as np
from nltk.corpus import stopwords
from nltk.corpus import wordnet
from nltk.stem.wordnet import WordNetLemmatizer
import stanza
from finbert_embedding.embedding import FinbertEmbedding
from scipy.spatial.distance import cosine

In [2]:
# url = 'https://www.federalreserve.gov/monetarypolicy/fomcminutes20210127.htm'
# html = request.urlopen(url).read().decode('utf8')
# raw = BeautifulSoup(html, 'html.parser').get_text()
# nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')
nltk.download('stopwords')
nltk.download('punkt')
# stanza.download('en')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /home/sarahwang688/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /home/sarahwang688/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /home/sarahwang688/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [3]:
text_raw_data = pd.read_csv('fed_speeches_1996_2020.csv')
text_raw_data = text_raw_data.loc[text_raw_data.year>2010]
# text_str = text_raw_data.text.str.cat()
# text_str = text_str.lower()
# tokens = sent_tokenize(text_str)


In [4]:
# pd.DataFrame(tokens[:2])

In [5]:
sentence_df = pd.DataFrame()
for index, row in text_raw_data.iterrows():
    tokens = sent_tokenize(row.text)
    tokens_df = pd.DataFrame(tokens)
    tokens_df.columns = ['sentence']
    tokens_df['date'] = row.date
    sentence_df = pd.concat([sentence_df, tokens_df], axis = 0)
sentence_df.sentence = sentence_df.sentence.str.lower()

In [6]:

sentence_df = sentence_df[~sentence_df.sentence.str.contains('return to text')]
sentence_df = sentence_df.reset_index(drop=True)
sentence_df

sentence        date
0                                          good morning.  20111129.0
1      i'm delighted to return "home" to the federal ...  20111129.0
2      in my remarks this morning i will underscore t...  20111129.0
3      the global economy is facing critical challenges.  20111129.0
4      the recovery in the united states and other ad...  20111129.0
...                                                  ...         ...
62874  the bank's ratio would be compared to a minimu...  20200108.0
62875  the minimum activity threshold would be calibr...  20200108.0
62876  board of governors of the federal reserve syst...  20200108.0
62877  lael brainard, "the community reinvestment act...  20200108.0
62878  statewide activity outside of a bank's local a...  20200108.0

[62879 rows x 2 columns]

In [7]:
finbert = FinbertEmbedding()

In [8]:
# word_embedding = finbert.word_vector(tokens[0])
# sentence_embedding = finbert.sentence_vector(tokens[0])
# sentence_embedding

In [9]:
# word_embedding

In [10]:
aspects_list = ['inflation', 'growth', 'employment','unemployment', 'economic'] # interest rate
aspects = ' '.join(aspects_list)

In [11]:
aspect_embedding = finbert.word_vector(aspects)
aspect_embedding

[tensor([-2.6459e+00,  5.0577e+00,  7.0270e-01,  6.5040e-01,  4.9906e+00,
          2.9770e+00, -1.3743e+00,  5.8993e+00, -4.9724e+00, -3.9156e+00,
          3.5263e-01,  1.3959e+00, -4.7064e-01, -5.8541e-01,  6.8146e-01,
          2.7232e+00,  2.3346e+00, -1.2383e+00, -9.8738e-01,  8.3338e-01,
          1.4785e+00, -4.5970e-01,  2.7338e+00,  2.9602e+00,  1.0331e+00,
         -1.5216e+00,  7.9723e-01,  3.5460e+00, -5.2738e-01,  2.2141e+00,
          1.1490e+00,  9.7620e-01,  1.1171e+00,  1.3401e+00,  2.7022e+00,
         -1.6402e+00, -1.7449e+00,  1.7813e+00, -1.0548e+00,  9.6534e-01,
          2.0486e+00, -6.1366e+00,  6.8627e-01, -1.3549e-01,  9.3733e-02,
         -2.0719e+00, -2.1430e+00, -4.4645e+00, -2.3267e+00, -4.9708e+00,
         -1.0494e+00, -1.0582e+00, -1.2235e+00, -5.0577e-01,  1.6591e+00,
          3.0397e+00, -2.7183e-01, -1.3363e+00, -1.5930e+00,  1.9407e+00,
         -1.0185e-01,  6.5754e-03, -1.9990e+00, -6.0494e-01, -2.7745e+00,
          1.8681e-01,  2.4290e+00,  5.

In [12]:
# sentence_embedding

In [13]:
def calc_cos_distance(sentence_embedding):
    cos_list = []
    for i in np.arange(len(aspects_list)):
        cos = 1-cosine(sentence_embedding, aspect_embedding[i])
        cos_list = cos_list + [cos]
    print(cos_list)
    return cos_list

In [14]:
cos_similiary = sentence_df.copy()
for aspect in aspects_list:
    cos_similiary[aspect] = np.nan
cos_similiary

sentence        date  \
0                                          good morning.  20111129.0   
1      i'm delighted to return "home" to the federal ...  20111129.0   
2      in my remarks this morning i will underscore t...  20111129.0   
3      the global economy is facing critical challenges.  20111129.0   
4      the recovery in the united states and other ad...  20111129.0   
...                                                  ...         ...   
62874  the bank's ratio would be compared to a minimu...  20200108.0   
62875  the minimum activity threshold would be calibr...  20200108.0   
62876  board of governors of the federal reserve syst...  20200108.0   
62877  lael brainard, "the community reinvestment act...  20200108.0   
62878  statewide activity outside of a bank's local a...  20200108.0   

       inflation  growth  employment  unemployment  economic  
0            NaN     NaN         NaN           NaN       NaN  
1            NaN     NaN         NaN           NaN       NaN  
2            NaN     NaN         NaN           NaN       NaN  
3            NaN     NaN         NaN           NaN       NaN  
4            NaN     NaN         NaN           NaN       NaN  
...          ...     ...         ...           ...       ...  
62874        NaN     NaN         NaN           NaN       NaN  
62875        NaN     NaN         NaN           NaN       NaN  
62876        NaN     NaN         NaN           NaN       NaN  
62877        NaN     NaN         NaN           NaN       NaN  
62878        NaN     NaN         NaN           NaN       NaN  

[62879 rows x 7 columns]

In [15]:
# aspects_list = ['inflation', 'growth', 'employment','unemployment', 'economic'] 
for index, row in cos_similiary.iterrows():
    print(index)
    sentence_embedding = finbert.sentence_vector(row.sentence)
    cos = calc_cos_distance(sentence_embedding)
    cos_similiary.loc[index, 'inflation'] = cos[0]
    cos_similiary.loc[index, 'growth'] = cos[1]
    cos_similiary.loc[index, 'employment'] = cos[2]
    cos_similiary.loc[index, 'unemployment'] = cos[3]
    cos_similiary.loc[index, 'economic'] = cos[4]

0
[0.18773433566093445, 0.20308564603328705, 0.1938304305076599, 0.22041690349578857, 0.21034646034240723]
1
[0.28252705931663513, 0.345718652009964, 0.33066326379776, 0.31483641266822815, 0.2508467733860016]
2
[0.285919189453125, 0.35803186893463135, 0.32202282547950745, 0.3115590810775757, 0.2444530427455902]
3
[0.30484816431999207, 0.35220903158187866, 0.33947280049324036, 0.3379825949668884, 0.27774283289909363]
4
[0.33045056462287903, 0.40473052859306335, 0.4229705035686493, 0.39448362588882446, 0.30786943435668945]
5
[0.2980571389198303, 0.37940752506256104, 0.32311302423477173, 0.29225480556488037, 0.26604342460632324]
6
[0.3548319339752197, 0.4184199273586273, 0.3778091073036194, 0.3781067430973053, 0.3146490752696991]
7
[0.2590642273426056, 0.32895076274871826, 0.30727407336235046, 0.2969067096710205, 0.2873179018497467]
8
[0.33247363567352295, 0.3883674144744873, 0.34107890725135803, 0.34029510617256165, 0.27473220229148865]
9
[0.34233444929122925, 0.42167606949806213, 0.3994

[0.2994286119937897, 0.38129478693008423, 0.3424050211906433, 0.31567811965942383, 0.2824658453464508]
79
[0.3198353350162506, 0.4062438905239105, 0.3537222146987915, 0.3229881823062897, 0.30092862248420715]
80
[0.32111480832099915, 0.4112672209739685, 0.3826845586299896, 0.3509843051433563, 0.3017791509628296]
81
[0.28747454285621643, 0.3469519019126892, 0.31536391377449036, 0.31406500935554504, 0.283137708902359]
82
[0.3739594519138336, 0.4423160254955292, 0.4306206703186035, 0.3961901068687439, 0.3275239169597626]
83
[0.29595616459846497, 0.3800280690193176, 0.34553399682044983, 0.32245129346847534, 0.2722543776035309]
84
[0.3104529082775116, 0.4127829670906067, 0.40479469299316406, 0.3557872474193573, 0.3208993673324585]
85
[0.3431299030780792, 0.4548463821411133, 0.4187760353088379, 0.3771282434463501, 0.3253024220466614]
86
[0.29381969571113586, 0.3765573799610138, 0.3567047119140625, 0.33497723937034607, 0.296481728553772]
87
[0.3481397330760956, 0.426009863615036, 0.38163444399

[0.3111790418624878, 0.38455119729042053, 0.34581491351127625, 0.33144882321357727, 0.30386215448379517]
157
[0.28431740403175354, 0.3403245508670807, 0.31381335854530334, 0.3222915232181549, 0.29091495275497437]
158
[0.3004303276538849, 0.37229397892951965, 0.33434176445007324, 0.32830172777175903, 0.2971762418746948]
159
[0.29023274779319763, 0.3647444546222687, 0.34038621187210083, 0.32539182901382446, 0.31003907322883606]
160
[0.2894563674926758, 0.3824361264705658, 0.34686535596847534, 0.3410089612007141, 0.30663105845451355]
161
[0.2638784945011139, 0.317210853099823, 0.2898985743522644, 0.2970094680786133, 0.2533721923828125]
162
[0.29192474484443665, 0.3459870517253876, 0.3058437407016754, 0.31130272150039673, 0.28604841232299805]
163
[0.31904080510139465, 0.3996318280696869, 0.35764387249946594, 0.3593059182167053, 0.3419525623321533]
164
[0.29906922578811646, 0.3751163184642792, 0.33531832695007324, 0.34320080280303955, 0.3125973045825958]
165
[0.27434098720550537, 0.37449252

[0.30948659777641296, 0.38585102558135986, 0.34519684314727783, 0.34627652168273926, 0.2947080433368683]
234
[0.3340235650539398, 0.3971833884716034, 0.34640008211135864, 0.34430575370788574, 0.2950339615345001]
235
[0.3340235948562622, 0.39661285281181335, 0.35749951004981995, 0.3592139780521393, 0.30796220898628235]
236
[0.21789662539958954, 0.255901962518692, 0.25568902492523193, 0.26571688055992126, 0.1915961652994156]
237
[0.22533570230007172, 0.2828187346458435, 0.27675125002861023, 0.27645981311798096, 0.2161654829978943]
238
[0.21821998059749603, 0.2567615211009979, 0.24278685450553894, 0.25654366612434387, 0.19799001514911652]
239
[0.260399729013443, 0.32063016295433044, 0.33318889141082764, 0.3387860357761383, 0.2663779556751251]
240
[0.19809328019618988, 0.24278509616851807, 0.23861412703990936, 0.24847052991390228, 0.18653514981269836]
241
[0.3122006356716156, 0.3656959533691406, 0.3587321937084198, 0.36821264028549194, 0.2845189869403839]
242
[0.2759682834148407, 0.3486698

[0.28424495458602905, 0.37923988699913025, 0.377672016620636, 0.33810707926750183, 0.28401491045951843]
311
[0.29428595304489136, 0.3989720046520233, 0.398380845785141, 0.35345953702926636, 0.3102639615535736]
312
[0.28626203536987305, 0.3736411929130554, 0.37104424834251404, 0.3352341055870056, 0.27865052223205566]
313
[0.32943373918533325, 0.39652395248413086, 0.37363722920417786, 0.35587871074676514, 0.2899746596813202]
314
[0.3630841374397278, 0.42220932245254517, 0.38422244787216187, 0.36392107605934143, 0.3054318428039551]
315
[0.18407082557678223, 0.21596787869930267, 0.2116428166627884, 0.2194858342409134, 0.1651601791381836]
316
[0.19815978407859802, 0.21929922699928284, 0.20733830332756042, 0.23267492651939392, 0.16391527652740479]
317
[0.27215877175331116, 0.2581939697265625, 0.22693073749542236, 0.2541324496269226, 0.3216145932674408]
318
[0.33238816261291504, 0.3693855404853821, 0.37300318479537964, 0.3712518811225891, 0.3065113127231598]
319
[0.3652029037475586, 0.4054520

...

[0.28157779574394226, 0.3275444507598877, 0.3070407807826996, 0.29798558354377747, 0.253946453332901]
62527
[0.25936418771743774, 0.3098084330558777, 0.3031228184700012, 0.30788666009902954, 0.2641837000846863]
62528
[0.2696387469768524, 0.3282538056373596, 0.312883198261261, 0.3034568130970001, 0.24445344507694244]
62529
[0.2726529538631439, 0.3254742920398712, 0.2804299294948578, 0.29244163632392883, 0.26509785652160645]
62530
[0.3219229280948639, 0.3975096344947815, 0.354157030582428, 0.33678391575813293, 0.30785268545150757]
62531
[0.2797375023365021, 0.3457408845424652, 0.3137344419956207, 0.3051522970199585, 0.26046472787857056]
62532
[0.2863360047340393, 0.37609732151031494, 0.35118043422698975, 0.35802167654037476, 0.3035709857940674]
62533
[0.2877759635448456, 0.35113048553466797, 0.3394893705844879, 0.3449864089488983, 0.27483776211738586]
62534
[0.3097406327724457, 0.34611275792121887, 0.32053589820861816, 0.3278622627258301, 0.2724994122982025]
62535
[0.28855812549591064, 0

[0.31089064478874207, 0.366000235080719, 0.3189961314201355, 0.3350948095321655, 0.2911854088306427]
62603
[0.29063597321510315, 0.3825431764125824, 0.35176417231559753, 0.3387083411216736, 0.2912873923778534]
62604
[0.3110739588737488, 0.37371164560317993, 0.3396540582180023, 0.34202060103416443, 0.2946230471134186]
62605
[0.27382805943489075, 0.31585612893104553, 0.3172459304332733, 0.3277037739753723, 0.2607087790966034]
62606
[0.292978435754776, 0.3201102018356323, 0.2997828722000122, 0.32463693618774414, 0.24771936237812042]
62607
[0.2763441801071167, 0.346476674079895, 0.2965049147605896, 0.3171575963497162, 0.2597609758377075]
62608
[0.33434003591537476, 0.389027863740921, 0.3494953215122223, 0.37159043550491333, 0.3226567506790161]
62609
[0.32086414098739624, 0.3966294229030609, 0.36676427721977234, 0.35987040400505066, 0.3234201669692993]
62610
[0.29813501238822937, 0.3532237112522125, 0.32315385341644287, 0.34361520409584045, 0.2945452034473419]
62611
[0.281846821308136, 0.32

[0.27838844060897827, 0.38683950901031494, 0.34388551115989685, 0.3181469440460205, 0.2668777406215668]
62679
[0.3469851315021515, 0.4409143924713135, 0.38310661911964417, 0.3544621169567108, 0.30182650685310364]
62680
[0.2563495934009552, 0.3166339099407196, 0.3138028085231781, 0.3165934681892395, 0.2571859657764435]
62681
[0.2942911386489868, 0.365220308303833, 0.3939898908138275, 0.36125075817108154, 0.2827085256576538]
62682
[0.3667061924934387, 0.4441790282726288, 0.4369966983795166, 0.412697434425354, 0.3199479281902313]
62683
[0.364627867937088, 0.44971325993537903, 0.4552808105945587, 0.40546146035194397, 0.3350290060043335]
62684
[0.3546130657196045, 0.43690788745880127, 0.46104875206947327, 0.4279724955558777, 0.33259233832359314]
62685
[0.32387852668762207, 0.42489415407180786, 0.4215138852596283, 0.37247005105018616, 0.3306441605091095]
62686
[0.32203319668769836, 0.3997206687927246, 0.4267856478691101, 0.3853985369205475, 0.3078046143054962]
62687
[0.3409801125526428, 0.45

[0.30941471457481384, 0.4111376106739044, 0.3839899003505707, 0.36370784044265747, 0.3280079662799835]
62755
[0.2261277437210083, 0.2688889503479004, 0.2613760828971863, 0.27491259574890137, 0.21111343801021576]
62756
[0.28032538294792175, 0.34064599871635437, 0.30835050344467163, 0.3166709840297699, 0.24880824983119965]
62757
[0.32836562395095825, 0.4064808785915375, 0.3689045310020447, 0.37950438261032104, 0.33545440435409546]
62758
[0.3227381408214569, 0.3921106159687042, 0.35204723477363586, 0.3467441499233246, 0.3006954789161682]
62759
[0.26905420422554016, 0.32974255084991455, 0.27682381868362427, 0.29016396403312683, 0.2605780065059662]
62760
[0.23320439457893372, 0.2731144428253174, 0.23654621839523315, 0.2661469578742981, 0.21473859250545502]
62761
[0.2721783518791199, 0.34102463722229004, 0.3177013397216797, 0.3269668221473694, 0.2917003929615021]
62762
[0.28452393412590027, 0.349797785282135, 0.3415308892726898, 0.3224574625492096, 0.29580000042915344]
62763
[0.2917099595069

[0.3001782298088074, 0.3882303535938263, 0.3424719572067261, 0.33544662594795227, 0.30802759528160095]
62831
[0.326499342918396, 0.406412273645401, 0.367961049079895, 0.34864452481269836, 0.3197205662727356]
62832
[0.29406383633613586, 0.33907392621040344, 0.3108179271221161, 0.30401021242141724, 0.25665083527565]
62833
[0.3379126191139221, 0.39992138743400574, 0.3764466941356659, 0.36117562651634216, 0.30941009521484375]
62834
[0.3283350467681885, 0.40499234199523926, 0.3850104808807373, 0.371174693107605, 0.31703612208366394]
62835
[0.33919113874435425, 0.42243292927742004, 0.41444963216781616, 0.4052221477031708, 0.3338263928890228]
62836
[0.3140115737915039, 0.3801499903202057, 0.34339597821235657, 0.3356917202472687, 0.285975843667984]
62837
[0.32277747988700867, 0.41750213503837585, 0.37960630655288696, 0.351166695356369, 0.2993733584880829]
62838
[0.25349271297454834, 0.3031832277774811, 0.2530018389225006, 0.2776073217391968, 0.22288765013217926]
62839
[0.27552300691604614, 0.3

In [22]:
cos_similiary


sentence        date  \
0                                          good morning.  20111129.0   
1      i'm delighted to return "home" to the federal ...  20111129.0   
2      in my remarks this morning i will underscore t...  20111129.0   
3      the global economy is facing critical challenges.  20111129.0   
4      the recovery in the united states and other ad...  20111129.0   
...                                                  ...         ...   
62874  the bank's ratio would be compared to a minimu...  20200108.0   
62875  the minimum activity threshold would be calibr...  20200108.0   
62876  board of governors of the federal reserve syst...  20200108.0   
62877  lael brainard, "the community reinvestment act...  20200108.0   
62878  statewide activity outside of a bank's local a...  20200108.0   

       inflation    growth  employment  unemployment  economic  
0       0.187734  0.203086    0.193830      0.220417  0.210346  
1       0.282527  0.345719    0.330663      0.314836  0.250847  
2       0.285919  0.358032    0.322023      0.311559  0.244453  
3       0.304848  0.352209    0.339473      0.337983  0.277743  
4       0.330451  0.404731    0.422971      0.394484  0.307869  
...          ...       ...         ...           ...       ...  
62874   0.284297  0.361377    0.320890      0.314664  0.253812  
62875   0.326488  0.386329    0.332340      0.351731  0.271299  
62876   0.308902  0.361910    0.336381      0.346712  0.306534  
62877   0.309505  0.386816    0.385695      0.375667  0.314872  
62878   0.294489  0.406110    0.362721      0.352318  0.320107  

[62879 rows x 7 columns]

In [25]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification
tokenizer = AutoTokenizer.from_pretrained("ProsusAI/finbert")

In [26]:
model = AutoModelForSequenceClassification.from_pretrained("ProsusAI/finbert")

In [41]:
from models.finBERT.finbert.finbert import predict

In [75]:
for index, row in cos_similiary.iterrows():
    
    max_aspect_value = row[aspects_list]
    aspect = max_aspect_value.loc[max_aspect_value==max_aspect_value.max()].index[0]
    cos_similiary.loc[index, 'aspect'] = aspect

In [42]:
test = cos_similiary.head(2)

In [57]:
max_aspect_value.loc[max_aspect_value==max_aspect_value.max()].index[0]

'growth'

In [76]:
cos_similiary

sentence        date  \
0                                          good morning.  20111129.0   
1      i'm delighted to return "home" to the federal ...  20111129.0   
2      in my remarks this morning i will underscore t...  20111129.0   
3      the global economy is facing critical challenges.  20111129.0   
4      the recovery in the united states and other ad...  20111129.0   
...                                                  ...         ...   
62874  the bank's ratio would be compared to a minimu...  20200108.0   
62875  the minimum activity threshold would be calibr...  20200108.0   
62876  board of governors of the federal reserve syst...  20200108.0   
62877  lael brainard, "the community reinvestment act...  20200108.0   
62878  statewide activity outside of a bank's local a...  20200108.0   

       inflation    growth  employment  unemployment  economic        aspect  
0       0.187734  0.203086    0.193830      0.220417  0.210346  unemployment  
1       0.282527  0.345719    0.330663      0.314836  0.250847        growth  
2       0.285919  0.358032    0.322023      0.311559  0.244453        growth  
3       0.304848  0.352209    0.339473      0.337983  0.277743        growth  
4       0.330451  0.404731    0.422971      0.394484  0.307869    employment  
...          ...       ...         ...           ...       ...           ...  
62874   0.284297  0.361377    0.320890      0.314664  0.253812        growth  
62875   0.326488  0.386329    0.332340      0.351731  0.271299        growth  
62876   0.308902  0.361910    0.336381      0.346712  0.306534        growth  
62877   0.309505  0.386816    0.385695      0.375667  0.314872        growth  
62878   0.294489  0.406110    0.362721      0.352318  0.320107        growth  

[62879 rows x 8 columns]

In [78]:
grouped = cos_similiary.groupby('aspect')
for name, group in grouped:
    group.sentence.to_csv(f'{name}.txt', header=None, index=None, sep=' ', mode='a')

In [91]:
with open('economic.txt', 'r') as f:
    text = f.read()

In [92]:
predict(text, model, write_to_csv = True, path = 'sent_embedding_economic_sentiment.csv')

sentence                                  logit prediction  \
0           1.    [0.03752543, 0.0374784, 0.92499614]    neutral   
1           1.    [0.03752543, 0.0374784, 0.92499614]    neutral   
2       50-51.  [0.031907465, 0.036748663, 0.9313439]    neutral   
3           1.    [0.03752543, 0.0374784, 0.92499614]    neutral   
4           1.    [0.03752543, 0.0374784, 0.92499614]    neutral   
...        ...                                    ...        ...   
1727        4.   [0.029252268, 0.04382017, 0.9269275]    neutral   
1728  1.\nreg.   [0.035603836, 0.03863402, 0.9257621]    neutral   
1729        1.    [0.03752543, 0.0374784, 0.92499614]    neutral   
1730        1.    [0.03752543, 0.0374784, 0.92499614]    neutral   
1731        1.    [0.03752543, 0.0374784, 0.92499614]    neutral   

      sentiment_score  
0            0.000047  
1            0.000047  
2           -0.004841  
3            0.000047  
4            0.000047  
...               ...  
1727        -0.014568  
1728        -0.003030  
1729         0.000047  
1730         0.000047  
1731         0.000047  

[1732 rows x 4 columns]